나중에 해봐야 할것
1. get 요청으로 html을 받는다
2. 받은 html 에서 CSRFToken 을 검색해 값을 찾는다.
 - CSRFToken 이 매번 바뀌니 갱신을 해야 한다
3. post 요청으로 CSRFToken 을 해더로 보낸다. 데이터를 받는다.

In [40]:
# 정의
# 부모 정의
from Crawling import Crawling

# 클레스 내 필요한거
import datetime as dt
import json
import sys

# 커스텀 클레스 정의
# 환경변수 등록
sys.path.append( r'C:\Users\SDA12\Desktop\AiWork' )

# 커스텀 모둘 업핸드
from De_to_En.EntoDe_code import EntoDe_code

class BoxOffice( Crawling ):

    def __init__(self) -> None:
        # 부모 생성자 호출
        super().__init__()

        # 속성 정의
        # self.js_data
        self.daily_data = {}
        pass # 생성자 끝

    def kobis_connect( self ):
                
        key = EntoDe_code().get_decoder( 'Yek.br' )

        # 하루전 날자를 받는다
        date_str = dt.datetime.now().strftime('%Y')  + str( dt.datetime.now().month ).zfill(2) + str( dt.datetime.now().day - 1 ).zfill(2)

        # 접속할 사이트
        URL = f'http://kobis.or.kr/kobisopenapi/webservice/rest/boxoffice/searchDailyBoxOfficeList.json?key={key}&targetDt={date_str}'

        self.url_connect( URL )

        # print( self.respoonse.text )

        # 사이트에서 받아온 값을 json 형식을 파일을 변환
        js_data = self.get_to_jsons()
        
        # json 형식의 파일 안에서 boxOfficeResult에 dailyBoxOfficeList의 데이터를 가져옴
        # daily_data의 딕셔너리에 키 값으로 날자( YYYYMMDD 형식 ) 넣고 
        # 데이터 값에 boxOfficeResult에 dailyBoxOfficeList의 데이터를 리스트 형식으로 넣는다
        self.daily_data = { date_str : js_data[ 'boxOfficeResult']['dailyBoxOfficeList' ] }

        pass # kobis_connect 끝

    # 데이터 출력
    def top10_print( self ):

        out_str = ''
        # 출력 반복문
        for day in self.daily_data:  # 딕셔너리 저근 for 문
            for data in self.daily_data[ day ]:  # 리스트 접근 for 문
                n_or_o = '' # 문자열을 저장할 임시변수
                # data['rankOldAndNew']의 값에 따라 기존 와 신규를 임시변수에 저장
                if data['rankOldAndNew'] == 'OLD':
                    n_or_o = '기존'
                else:
                    n_or_o = '신규'
                
                # 순위와 영화 이름 그리고 신규 또는 기존으로 출력
                # print( data['rank'] + ' ' + data['movieNm'] + ' ' + n_or_o  )
                out_str += data['rank'] + ' ' + data['movieNm'] + ' ' + n_or_o + '\n'
                pass # data for 문 끝
            pass # day for 문 끝
        return out_str
        pass # top10_print 끝

    def new_movie( self ) -> bool:
        """
        새 영화가 있으면 True, 없으면 False 를 반환
        """
        # 새로운 영화 있는지 탐색
        for day in self.daily_data:  # 딕셔너리 접근 for 문
            for idx in self.daily_data[ day ]:     # 리스트 접근 for 문
                
                # # print( self.daily_data[ day ] )    
                # print( idx )
                # break
                # 새영화가 있는지 탐색
                if idx['rankOldAndNew'] == 'NEW':
                    print( '새영화 발견, 메세지를 보냅니다.' )
                    return True                    
                    pass
                pass            # 리스트 접근 for 문 종료
            pass                # 딕셔너리 접근 for 문 종료
        return False
        pass # new_save 끝

    def new_save( self ):
        """
        새 영화가 있으면 영화를 저장 하고 아니면 저장 하지 않는다.
        """
        # 새로운 영화 있는지 탐색
        for day in self.daily_data:  # 딕셔너리 접근 for 문
            for idx in self.daily_data[ day ]:     # 리스트 접근 for 문
                
                # # print( self.daily_data[ day ] )    
                # print( idx )
                # break
                # 새영화가 있는지 탐색
                if idx['rankOldAndNew'] == 'NEW':
                    print( '새영화 발견, 데이터를 저장 합니다.' )
                    # 저장된 파일을 가져온다
                    f = open( 'BoxOffice.sav', 'r' )
                    # 가져온 데이터를 json 형식으로 불러온다
                    load_json = json.load( f )
                    f.close()   # 파일 닫기
                    
                    # 새로 받은 데이터에서 키값을 추출
                    # 어느 순서가 되었든 마지막 것만 가져온다
                    li_key = list( self.daily_data.keys() )[-1]  
                    # 기존 데이터에 업데이트 되는 데이터를 추가한다.
                    load_json[ li_key ] = self.daily_data[ li_key ] 
                    
                    # 파일을 불러오기
                    f = open( 'BoxOffice.sav', 'w' )
                    json.dump( load_json, f )   # 기존 데이터에 새 데이터 덮어쓰기
                    f.close()   # 파일 닫기

                    break   # 새영화가 있는지 탐색을 끝내고 모든 반복문 종료
                    pass
                pass            # 리스트 접근 for 문 종료
            pass                # 딕셔너리 접근 for 문 종료
        pass # new_save 끝

    def main( self ):

        self.kobis_connect()

        self.top10_print()

        # self.new_save()

        pass # main 끝

    pass # BoxOffice 끝

box_of = BoxOffice().main()



1 파묘 기존
2 듄: 파트2 기존
3 웡카 기존
4 브레드이발소: 셀럽 인 베이커리타운 기존
5 건국전쟁 기존
6 아이엠 티라노 기존
7 귀멸의 칼날: 인연의 기적, 그리고 합동 강화 훈련으로 기존
8 소풍 기존
9 사운드 오브 프리덤 기존
10 패스트 라이브즈 기존


In [25]:
str( dt.datetime.now().month -0 ).zfill(2)

'03'

In [11]:
# # 만들었던 크롤링 부분을 클레스화?
# # 정의
# import requests
# import json
# from bs4 import BeautifulSoup

# # Crawling
# class Crawling:

#     def __init__(self) -> None:
#         """
#         생성자
#         """
#         self.respoonse = requests

#         pass # 생성자 끝

#     def url_connect( self, URL ) -> int:
#         """
#         URL : str, 접속할 사이트주소
#         reutnr : int, respoonse 상태를 알려준다.
#         """

#         # 사이트에 요청
#         self.respoonse = requests.get( URL, headers = {} )
#         return self.get_states()        
#         pass # 메소드 get_connect

#     def get_states( self ) -> int:
#         """
#         respoonse 상태를 알려준다.
#         """
#         return self.respoonse.status_code
#         pass # get_res_states 

#     def get_text( self ) -> str:
#         """
#         respoonse의 속성의 텍스트를 넘겨준다
#         """
#         return self.respoonse.text
#         pass # get_text 끝

#     def get_to_json( self ):
#         """
#         respoonse를 json 형태로 파싱한 데이터를 넘겨준다
#         """
#         return json.load( self.respoonse.text )
#         pass # get_to_json 끝
    
#     def get_to_soup( self ):
#         """
#         respoonse를 BeautifulSoup 형태로 파싱한 데이터를 넘겨준다
#         """
#         return BeautifulSoup( self.respoonse.text, 'html.parser' )
#         pass # get_to_soup 끝

#     pass # class Crawling 끝

In [24]:
# API를 이용해서 데이터 받아오기
import requests
import datetime as dt
import json
import sys

# 환경변수 등록
sys.path.append( r'C:\Users\SDA12\Desktop\AiWork' )

# 커스텀 모둘 업핸드
from De_to_En.EntoDe_code import EntoDe_code


# f = open( 'Yek.br', 'r', encoding='utf-8' )
# key = f.read()
# f.close()
key = EntoDe_code().get_decoder( 'Yek.br' )

# 하루전 날자를 받는다
date_str = dt.datetime.now().strftime('%Y%m')  + str( dt.datetime.now().day -1 ).zfill(2)

# 접속할 사이트
URL = f'http://kobis.or.kr/kobisopenapi/webservice/rest/boxoffice/searchDailyBoxOfficeList.json?key={key}&targetDt={date_str}'

key

# 사이트에 요청
respoonse = requests.get(URL, headers = {} )

# 사이트에서 받아온 값을 json 형식을 파일을 변환
js_data = json.loads( respoonse.text )

# json 형식의 파일 안에서 boxOfficeResult에 dailyBoxOfficeList의 데이터를 가져옴
# daily_data의 딕셔너리에 키 값으로 날자( YYYYMMDD 형식 ) 넣고 
# 데이터 값에 boxOfficeResult에 dailyBoxOfficeList의 데이터를 리스트 형식으로 넣는다
daily_data = { date_str : js_data[ 'boxOfficeResult']['dailyBoxOfficeList' ] }

# daily_data[ '02342485' ] = 13

# 데이터 출력
for day in daily_data:  # 딕셔너리 저근 for 문
    # if day.get('day', 0):
        # continue
    for data in daily_data[ day ]:  # 리스트 접근 for 문
        n_or_o = ''
        if data['rankOldAndNew'] == 'OLD':
            n_or_o = '기존'
        else:
            n_or_o = '신규'
            
        print( data['rank'] + ' ' + data['movieNm'] + ' ' + n_or_o  )
        pass
    pass

# 새로운 영화 있는지 탐색
for day in daily_data:  # 딕셔너리 접근 for 문
    for idx in day:     # 리스트 접근 for 문
        # 새영화가 있는지 탐색
        if data['rankOldAndNew'] == 'NEW':
            print( '새영화 발견, 데이터를 저장 합니다.' )
            # 저장된 파일을 가져온다
            f = open( 'BoxOffice.sav', 'r' )
            # 가져온 데이터를 json 형식으로 불러온다
            load_json = json.load( f )
            f.close()   # 파일 닫기
            
            # 새로 받은 데이터에서 키값을 추출
            # 어느 순서가 되었든 마지막 것만 가져온다
            li_key = list( daily_data.keys() )[-1]  
            # 기존 데이터에 업데이트 되는 데이터를 추가한다.
            load_json[ li_key ] = daily_data[ li_key ] 
            
            # 파일을 불러오기
            f = open( 'BoxOffice.sav', 'w' )
            json.dump( load_json, f )   # 기존 데이터에 새 데이터 덮어쓰기
            f.close()   # 파일 닫기

            break   # 새영화가 있는지 탐색을 끝내고 모든 반복문 종료
            pass
        pass            # 리스트 접근 for 문 종료
    pass                # 딕셔너리 접근 for 문 종료

str_data =  str( daily_data )

# print( str_data )
str_data

1 파묘 기존
2 듄: 파트2 기존
3 웡카 기존
4 브레드이발소: 셀럽 인 베이커리타운 기존
5 건국전쟁 기존
6 아이엠 티라노 기존
7 귀멸의 칼날: 인연의 기적, 그리고 합동 강화 훈련으로 기존
8 소풍 기존
9 사운드 오브 프리덤 기존
10 패스트 라이브즈 기존


"{'20240303': [{'rnum': '1', 'rank': '1', 'rankInten': '0', 'rankOldAndNew': 'OLD', 'movieCd': '20234675', 'movieNm': '파묘', 'openDt': '2024-02-22', 'salesAmt': '6391631388', 'salesShare': '69.4', 'salesInten': '-1781765680', 'salesChange': '-21.8', 'salesAcc': '58008168139', 'audiCnt': '652065', 'audiInten': '-180219', 'audiChange': '-21.7', 'audiAcc': '6033209', 'scrnCnt': '2363', 'showCnt': '9539'}, {'rnum': '2', 'rank': '2', 'rankInten': '0', 'rankOldAndNew': 'OLD', 'movieCd': '20236295', 'movieNm': '듄: 파트2', 'openDt': '2024-02-28', 'salesAmt': '1665473640', 'salesShare': '18.1', 'salesInten': '-486312494', 'salesChange': '-22.6', 'salesAcc': '9040704194', 'audiCnt': '146003', 'audiInten': '-43748', 'audiChange': '-23.1', 'audiAcc': '820800', 'scrnCnt': '1097', 'showCnt': '3396'}, {'rnum': '3', 'rank': '3', 'rankInten': '0', 'rankOldAndNew': 'OLD', 'movieCd': '20236180', 'movieNm': '웡카', 'openDt': '2024-01-31', 'salesAmt': '462925536', 'salesShare': '5.0', 'salesInten': '-95730622',

In [3]:
# from De_to_En.EntoDe_code import EntoDe_code 
# # from De_to_En.EntoDe_code #  De_to_En.EntoDe_code = De_to_En 폴더의 . 으로 하위폴더의 EntoDe_code 파일이름 까지 정의
# # import EntoDe_code 클레스 정의

# key = EntoDe_code().get_decoder( 'Yek.br' )

# key

'4b751f46541adca1138efad7fbc79ccd'

In [ ]:
# 시스템 import
import sys

# 환경변수 등록
# sys.path.append('C:/Users/user/Desktop/study/De_to_En')
sys.path.append( r'C:\Users\SDA12\Desktop\AiWork' )
# r'C:\Users\SDA12\Desktop\AiWork' 윈도우에서는 폴더 경계가 \ 표시기 때문 r로 인식시켜준다.

# 파일 위치 정의 및 클래스 정의
from De_to_En.EntoDe_code import EntoDe_code

EnDcode = EntoDe_code()


In [4]:
# 시스템 import
import sys

# 환경변수 등록
# sys.path.append('C:/Users/user/Desktop/study/De_to_En')
sys.path.append( r'C:\Users\SDA12\Desktop\AiWork' )
# r'C:\Users\SDA12\Desktop\AiWork' 윈도우에서는 폴더 경계가 \ 표시기 때문 r로 인식시켜준다.

# 파일 위치 정의 및 클래스 정의
from De_to_En.EntoDe_code import EntoDe_code

EnDcode = EntoDe_code()

In [10]:
# 2진수 문자열을 받아서 10진수 문자열로 변환 시켜준다
def Decod2to10( bin_num ):

    # 문자열이 아니면 종료
    if type( bin_num ) != str:
        return

    # 결과 값을 저장할 변수
    li_num = []

    # 문자열 길이만큼 8씩 건너뛰어서 돌아감
    for i in range( 0, len(bin_num), 8):
        # 2진수를 10진수로 변환 하여 리스트에 추가
        li_num.append( chr( int(bin_num[i:i+8], 2 ) ) )

        pass
    # 분리된 문자열을 하나로 합처줌
    li_num = ''.join( li_num )
    return li_num       # 결과 리턴

In [10]:
type( respoonse.status_code )

int

In [25]:
respoonse.text

'{"boxOfficeResult":{"boxofficeType":"일별 박스오피스","showRange":"20240303~20240303","dailyBoxOfficeList":[{"rnum":"1","rank":"1","rankInten":"0","rankOldAndNew":"OLD","movieCd":"20234675","movieNm":"파묘","openDt":"2024-02-22","salesAmt":"6391631388","salesShare":"69.4","salesInten":"-1781765680","salesChange":"-21.8","salesAcc":"58008168139","audiCnt":"652065","audiInten":"-180219","audiChange":"-21.7","audiAcc":"6033209","scrnCnt":"2363","showCnt":"9539"},{"rnum":"2","rank":"2","rankInten":"0","rankOldAndNew":"OLD","movieCd":"20236295","movieNm":"듄: 파트2","openDt":"2024-02-28","salesAmt":"1665473640","salesShare":"18.1","salesInten":"-486312494","salesChange":"-22.6","salesAcc":"9040704194","audiCnt":"146003","audiInten":"-43748","audiChange":"-23.1","audiAcc":"820800","scrnCnt":"1097","showCnt":"3396"},{"rnum":"3","rank":"3","rankInten":"0","rankOldAndNew":"OLD","movieCd":"20236180","movieNm":"웡카","openDt":"2024-01-31","salesAmt":"462925536","salesShare":"5.0","salesInten":"-95730622","sal

In [12]:
js_data

{'boxOfficeResult': {'boxofficeType': '일별 박스오피스',
  'showRange': '20240228~20240228',
  'dailyBoxOfficeList': [{'rnum': '1',
    'rank': '1',
    'rankInten': '0',
    'rankOldAndNew': 'OLD',
    'movieCd': '20234675',
    'movieNm': '파묘',
    'openDt': '2024-02-22',
    'salesAmt': '3082228642',
    'salesShare': '59.0',
    'salesInten': '245556266',
    'salesChange': '8.7',
    'salesAcc': '31464198045',
    'audiCnt': '384605',
    'audiInten': '86139',
    'audiChange': '28.9',
    'audiAcc': '3312970',
    'scrnCnt': '1885',
    'showCnt': '7156'},
   {'rnum': '2',
    'rank': '2',
    'rankInten': '3',
    'rankOldAndNew': 'OLD',
    'movieCd': '20236295',
    'movieNm': '듄: 파트2',
    'openDt': '2024-02-28',
    'salesAmt': '1447201430',
    'salesShare': '27.7',
    'salesInten': '1327081800',
    'salesChange': '1104.8',
    'salesAcc': '1596871060',
    'audiCnt': '152956',
    'audiInten': '146129',
    'audiChange': '2140.5',
    'audiAcc': '161613',
    'scrnCnt': '1544',

In [3]:
# API를 이용해서 데이터 받아오기
import requests
import datetime as dt
import json

f = open( 'Yek.br', 'r', encoding='utf-8' )
key = f.read()
f.close()
key = Decod2to10( key )

# 하루전 날자를 받는다
date_str = dt.datetime.now().strftime('%Y%m')  + str( dt.datetime.now().day -1 )

# 접속할 사이트
URL = f'http://kobis.or.kr/kobisopenapi/webservice/rest/boxoffice/searchDailyBoxOfficeList.json?key={key}&targetDt={date_str}'

# 사이트에 요청
respoonse = requests.get(URL, headers = {} )

# 사이트에서 받아온 값을 json 형식을 파일을 변환
js_data = json.loads( respoonse.text )

# json 형식의 파일 안에서 boxOfficeResult에 dailyBoxOfficeList의 데이터를 가져옴
# daily_data의 딕셔너리에 키 값으로 날자( YYYYMMDD 형식 ) 넣고 
# 데이터 값에 boxOfficeResult에 dailyBoxOfficeList의 데이터를 리스트 형식으로 넣는다
daily_data = { date_str : js_data['boxOfficeResult']['dailyBoxOfficeList'] }

# daily_data[ '02342485' ] = 13

# 데이터 출력
for day in daily_data:  # 딕셔너리 저근 for 문
    # if day.get('day', 0):
        # continue
    for data in daily_data[ day ]:  # 리스트 접근 for 문
        n_or_o = ''
        if data['rankOldAndNew'] == 'OLD':
            n_or_o = '기존'
        else:
            n_or_o = '신규'
            
        print( data['rank'] + ' ' + data['movieNm'] + ' ' + n_or_o  )
        pass
    pass

# 새로운 영화 있는지 탐색
for day in daily_data:  # 딕셔너리 접근 for 문
    for idx in day:     # 리스트 접근 for 문
        # 새영화가 있는지 탐색
        if data['rankOldAndNew'] == 'NEW':
            print( '새영화 발견, 데이터를 저장 합니다.' )
            # 저장된 파일을 가져온다
            f = open( 'BoxOffice.sav', 'r' )
            # 가져온 데이터를 json 형식으로 불러온다
            load_json = json.load( f )
            f.close()   # 파일 닫기
            
            # 새로 받은 데이터에서 키값을 추출
            # 어느 순서가 되었든 마지막 것만 가져온다
            li_key = list( daily_data.keys() )[-1]  
            # 기존 데이터에 업데이트 되는 데이터를 추가한다.
            load_json[ li_key ] = daily_data[ li_key ] 
            
            # 파일을 불러오기
            f = open( 'BoxOffice.sav', 'w' )
            json.dump( load_json, f )   # 기존 데이터에 새 데이터 덮어쓰기
            f.close()   # 파일 닫기

            break   # 새영화가 있는지 탐색을 끝내고 모든 반복문 종료
            pass
        pass            # 리스트 접근 for 문 종료
    pass                # 딕셔너리 접근 for 문 종료

str_data =  str( daily_data )

# print( str_data )
str_data

KeyError: 'boxOfficeResult'

In [ ]:
# API를 사용하지 않고 파싱 하기import requests
import numpy as np
import datetime as dt
from bs4 import BeautifulSoup

# 크롤링 할 사이트 주소
URL = 'https://www.kobis.or.kr/kobis/business/stat/boxs/findDailyBoxOfficeList.do'

# 사이트에 정보를 요청
respoonse = requests.post(URL, headers = {} )

# 받아온 정보를 BeautifulSoup 으로 파싱 할수 있는 데이터로 변환
soup = BeautifulSoup( respoonse.text, 'html.parser' )

# soup 안에서 input의 데이터를 찾는다
get_str = soup.find('input')

# get_str 타입을 str 형식으로 변환
tag_str = str(get_str)

# 문자열에서 필요한 문자열의 시작과 끝을 잘라서 가져옴
token = tag_str[ tag_str.index( 'value="' ) + len('value="') : -3 ]
print( token )

# 검색할 날자를 하루전으로 해서 받아옴
date_str = dt.datetime.now().strftime('%Y%m')  + str( dt.datetime.now().day -1 )

# 사이트에 보내야 할 데이터 구성을 만든다
datas = {
    'CSRFToken' : token,
    'loadEnd' : 0,
    'searchType' : 'search',
    'sSearchFrom' : date_str,
    'sSearchTo' : date_str,
    'sMultiMovieYn' : '',
    'sRepNationCd' : '',
    'sWideAreaCd' : '',
}

# 필요한 데이터를 입력하고 사이트에 자료 요청
respoonse = requests.post(URL, headers = {}, data=datas )

# HTML로 보내주는 자료를 BeautifulSoup로 변환
soup = BeautifulSoup( respoonse.text, 'html.parser' )

# HTML 자료중에서 tbody_0의 클레스를 찾아 temp_str에 저장
temp_str = soup.select( '#tbody_0' )

# 찾을 데이터를 저장할 변수
str_array = []

# temp_str[0]의 자료중 a 태그 들을 찾을 반복문
for a_tag in temp_str[0].select( 'a' ):
    # 찾은 a_tag를 str_array에 추가한다
    str_array.append( a_tag )
    pass

# 찾을 데이터를 저장할 변수
str_title = []
# str_array의 데이터에서 최종 데이터를 찾을 반복문
for title in str_array:
    # 임시 저장 문자열
    # temp = ''
    temp = str( title )
    # str_title에 데이터를 추가 한다
    str_title.append( temp[ 
        # title의 문자열의 시작 값을 얻고 title= 길이만큼 더해서 데이터 시작값을 찾는다
        # >의 문자열 시작 값을 얻고 "의 문자열 길이만큼 빼서 인덱스 끝값을 얻는다.
        temp.find( 'title' ) + len( 'title="' ) : temp.find( '>' ) -1 ] )
    # print( temp )
    # temp.find(title)
    pass

# 결과
str_title

urUnBrVbafkCFtLDhCsbYP0iUlxWsjfOE7jMIETJ7R4


['파묘',
 '듄: 파트2',
 '웡카',
 '건국전쟁',
 '귀멸의 칼날: 인연의 기적, 그리고 합동 강화 훈련으로',
 '소풍',
 '추락의 해부',
 '극장판 츠루네: 시작의 한 발',
 '월레스와 그로밋 더 클래식 컬렉션',
 '사운드 오브 프리덤']

In [ ]:
if type('ㄴㅁㄴㅇㄻ') == str:
    print('와 된다')

와 된다


새 실험 소스들

In [ ]:
# json 으로 불러온 현제 목록
daily_data
# json 으로 불러온 목록을 문자형으로 형변환 한것
str_data

"{'20240228': [{'rnum': '1', 'rank': '1', 'rankInten': '0', 'rankOldAndNew': 'OLD', 'movieCd': '20234675', 'movieNm': '파묘', 'openDt': '2024-02-22', 'salesAmt': '3082228642', 'salesShare': '59.0', 'salesInten': '245556266', 'salesChange': '8.7', 'salesAcc': '31464198045', 'audiCnt': '384605', 'audiInten': '86139', 'audiChange': '28.9', 'audiAcc': '3312970', 'scrnCnt': '1885', 'showCnt': '7156'}, {'rnum': '2', 'rank': '2', 'rankInten': '3', 'rankOldAndNew': 'OLD', 'movieCd': '20236295', 'movieNm': '듄: 파트2', 'openDt': '2024-02-28', 'salesAmt': '1447201430', 'salesShare': '27.7', 'salesInten': '1327081800', 'salesChange': '1104.8', 'salesAcc': '1596871060', 'audiCnt': '152956', 'audiInten': '146129', 'audiChange': '2140.5', 'audiAcc': '161613', 'scrnCnt': '1544', 'showCnt': '5047'}, {'rnum': '3', 'rank': '3', 'rankInten': '-1', 'rankOldAndNew': 'OLD', 'movieCd': '20236180', 'movieNm': '웡카', 'openDt': '2024-01-31', 'salesAmt': '295815963', 'salesShare': '5.7', 'salesInten': '-87245445', 'sa

In [ ]:
# 저장된 데이터와 현제 가저온 데이터를 합치는 실험
f = open( 'BoxOffice01.txt', 'r' )
load_json = json.load( f )
f.close()

load_json

{'20240228': [{'rnum': '1',
   'rank': '1',
   'rankInten': '0',
   'rankOldAndNew': 'OLD',
   'movieCd': '20234675',
   'movieNm': '파묘',
   'openDt': '2024-02-22',
   'salesAmt': '3082284642',
   'salesShare': '59.0',
   'salesInten': '245612266',
   'salesChange': '8.7',
   'salesAcc': '31464310045',
   'audiCnt': '384610',
   'audiInten': '86144',
   'audiChange': '28.9',
   'audiAcc': '3312979',
   'scrnCnt': '1885',
   'showCnt': '7156'},
  {'rnum': '2',
   'rank': '2',
   'rankInten': '3',
   'rankOldAndNew': 'OLD',
   'movieCd': '20236295',
   'movieNm': '듄: 파트2',
   'openDt': '2024-02-28',
   'salesAmt': '1447201430',
   'salesShare': '27.7',
   'salesInten': '1327081800',
   'salesChange': '1104.8',
   'salesAcc': '1596871060',
   'audiCnt': '152956',
   'audiInten': '146129',
   'audiChange': '2140.5',
   'audiAcc': '161613',
   'scrnCnt': '1544',
   'showCnt': '5047'},
  {'rnum': '3',
   'rank': '3',
   'rankInten': '-1',
   'rankOldAndNew': 'OLD',
   'movieCd': '20236180',


In [ ]:
li_key = list( daily_data.keys() )[-1]
load_json[ li_key ] = daily_data[ li_key ]
load_json

{'20240228': [{'rnum': '1',
   'rank': '1',
   'rankInten': '0',
   'rankOldAndNew': 'OLD',
   'movieCd': '20234675',
   'movieNm': '파묘',
   'openDt': '2024-02-22',
   'salesAmt': '3082228642',
   'salesShare': '59.0',
   'salesInten': '245556266',
   'salesChange': '8.7',
   'salesAcc': '31464198045',
   'audiCnt': '384605',
   'audiInten': '86139',
   'audiChange': '28.9',
   'audiAcc': '3312970',
   'scrnCnt': '1885',
   'showCnt': '7156'},
  {'rnum': '2',
   'rank': '2',
   'rankInten': '3',
   'rankOldAndNew': 'OLD',
   'movieCd': '20236295',
   'movieNm': '듄: 파트2',
   'openDt': '2024-02-28',
   'salesAmt': '1447201430',
   'salesShare': '27.7',
   'salesInten': '1327081800',
   'salesChange': '1104.8',
   'salesAcc': '1596871060',
   'audiCnt': '152956',
   'audiInten': '146129',
   'audiChange': '2140.5',
   'audiAcc': '161613',
   'scrnCnt': '1544',
   'showCnt': '5047'},
  {'rnum': '3',
   'rank': '3',
   'rankInten': '-1',
   'rankOldAndNew': 'OLD',
   'movieCd': '20236180',


In [ ]:
f = open( 'BoxOffice.sav', 'w' )
json.dump( load_json, f )
f.close()

In [ ]:
f = open( 'BoxOffice.sav', 'r' )
load01 = json.load( f )
f.close()

In [ ]:
load01

{'20240228': [{'rnum': '1',
   'rank': '1',
   'rankInten': '0',
   'rankOldAndNew': 'OLD',
   'movieCd': '20234675',
   'movieNm': '파묘',
   'openDt': '2024-02-22',
   'salesAmt': '3082228642',
   'salesShare': '59.0',
   'salesInten': '245556266',
   'salesChange': '8.7',
   'salesAcc': '31464198045',
   'audiCnt': '384605',
   'audiInten': '86139',
   'audiChange': '28.9',
   'audiAcc': '3312970',
   'scrnCnt': '1885',
   'showCnt': '7156'},
  {'rnum': '2',
   'rank': '2',
   'rankInten': '3',
   'rankOldAndNew': 'OLD',
   'movieCd': '20236295',
   'movieNm': '듄: 파트2',
   'openDt': '2024-02-28',
   'salesAmt': '1447201430',
   'salesShare': '27.7',
   'salesInten': '1327081800',
   'salesChange': '1104.8',
   'salesAcc': '1596871060',
   'audiCnt': '152956',
   'audiInten': '146129',
   'audiChange': '2140.5',
   'audiAcc': '161613',
   'scrnCnt': '1544',
   'showCnt': '5047'},
  {'rnum': '3',
   'rank': '3',
   'rankInten': '-1',
   'rankOldAndNew': 'OLD',
   'movieCd': '20236180',


In [ ]:
type( li_key )

str

In [ ]:
# 딕셔너리 키값 불러오는 실험
test_li = [ 1, 2, 3, 4, ]
test_dic = { 'k1' : 12, 'k2' : 24, 'k3' : test_li }

print( *test_dic.keys() )

# 리스트로 형변환해야 가져올수 있음 안하면 딕셔너리형 데이터값의 키값
indx = list( test_dic.keys() )
indx[-1]

k1 k2 k3


'k3'

In [ ]:
print( *test_dic.keys() )

k1 k2 k3


In [ ]:
indx = list( test_dic.keys() )
indx[-1]

'k3'

In [ ]:
# 새로운 영화 있는지 탐색
for day in daily_data:  # 딕셔너리 접근 for 문
    for idx in day:     # 리스트 접근 for 문
        print( data['rankOldAndNew'] )
        if data['rankOldAndNew'] == 'NEW':
            print( '새영화 발견' )
            # 저장된 데이터와 현제 가저온 데이터를 합치는 실험
            f = open( 'BoxOffice01.txt', 'r' )
            load_json = json.load( f )
            f.close()
            
            li_key = list( daily_data.keys() )[-1]
            load_json[ li_key ] = daily_data[ li_key ]
            
            f = open( 'test_save.txt', 'w' )
            json.dump( load_json, f )
            f.close()

            break
            pass
        pass            # # 리스트 접근 for 문 종료
    print()
    pass                # 딕셔너리 접근 for 문 종료

OLD
OLD
OLD
OLD
OLD
OLD
OLD
OLD



In [ ]:
bin?

Signature: bin(number, /)
Docstring:
Return the binary representation of an integer.

>>> bin(2796202)
'0b1010101010101010101010'
Type:      builtin_function_or_method

In [ ]:
a = bin(7)[2:]  # '0b111'에서 '0b'를 제거
print( type(a) )
a = a.zfill(4)  # 4자리수로 만들기 위해 0으로 채우기
print(a)
type( a )

<class 'str'>
0111


str

In [ ]:
# 키값 2진수 변환 실험
f = open( 'Yek.br', 'r', encoding='utf-8' )
key = f.read()
f.close()

In [8]:
# 키값 2진수 변환 실험
f = open( 'Yek.br', 'w', encoding='utf-8' )
f.write( key )
f.close()

In [ ]:
li_key = list( key )
li_key

['0',
 '0',
 '1',
 '1',
 '0',
 '1',
 '0',
 '0',
 '0',
 '1',
 '1',
 '0',
 '0',
 '0',
 '1',
 '0',
 '0',
 '0',
 '1',
 '1',
 '0',
 '1',
 '1',
 '1',
 '0',
 '0',
 '1',
 '1',
 '0',
 '1',
 '0',
 '1',
 '0',
 '0',
 '1',
 '1',
 '0',
 '0',
 '0',
 '1',
 '0',
 '1',
 '1',
 '0',
 '0',
 '1',
 '1',
 '0',
 '0',
 '0',
 '1',
 '1',
 '0',
 '1',
 '0',
 '0',
 '0',
 '0',
 '1',
 '1',
 '0',
 '1',
 '1',
 '0',
 '0',
 '0',
 '1',
 '1',
 '0',
 '1',
 '0',
 '1',
 '0',
 '0',
 '1',
 '1',
 '0',
 '1',
 '0',
 '0',
 '0',
 '0',
 '1',
 '1',
 '0',
 '0',
 '0',
 '1',
 '0',
 '1',
 '1',
 '0',
 '0',
 '0',
 '0',
 '1',
 '0',
 '1',
 '1',
 '0',
 '0',
 '1',
 '0',
 '0',
 '0',
 '1',
 '1',
 '0',
 '0',
 '0',
 '1',
 '1',
 '0',
 '1',
 '1',
 '0',
 '0',
 '0',
 '0',
 '1',
 '0',
 '0',
 '1',
 '1',
 '0',
 '0',
 '0',
 '1',
 '0',
 '0',
 '1',
 '1',
 '0',
 '0',
 '0',
 '1',
 '0',
 '0',
 '1',
 '1',
 '0',
 '0',
 '1',
 '1',
 '0',
 '0',
 '1',
 '1',
 '1',
 '0',
 '0',
 '0',
 '0',
 '1',
 '1',
 '0',
 '0',
 '1',
 '0',
 '1',
 '0',
 '1',
 '1',
 '0',
 '0',
 '1',
 '1'

In [1]:
# 10진수를 2진수로 바꾸어준다
def Encod10to2( in_str ):

    # 문자열이 아니면 종료
    if type( bin_num ) != str:
        return
    
    # 받은 문자열은 1비트씩 분할
    in_str = list( in_str )
    # 임시로 저장할 변수
    bin_num = []

    for toAskii in in_str:
        # 잘라진 키값을 아스키코드 와 2진수로 변환
        toas = bin( ord( toAskii ) )[2:] # 문자를 아스키코드 값 -> 2진수 변환
        toas = toas.zfill(8)    # 자리수를 8자리로 만들어준다
        # print( f'문자 : {toAskii}, 2진 숫자 : {toas}' )
        bin_num.append( toas )  # 변환된 문자를 리스트에 추가
        # break
        pass
    # 분할된 문자열을 하나로 합처준다
    bin_num = ''.join( bin_num )
    return bin_num # 결과값 리턴

In [ ]:
len(bin_num)

256

In [2]:
# def Decod2to10( bin_num ):
#     # 다시 10진수로 변환

#     li_num = []
#     for i in range( 0, len(bin_num), 8):
#         # li_num = []

#         li_num.append( chr( int(bin_num[i:i+8], 2 ) ) )
#         # print(i)

#         pass
#     li_num = ''.join( li_num )
#     return li_num


In [3]:
# key = '4b751f46541adca1138efad7fbc79ccd'

# 키값 2진수 변환 실험
f = open( 'Yek.br', 'r', encoding='utf-8' )
key = f.read()
f.close()

print( key )
a = Encod10to2( key )
b = Decod2to10( a )
print( b )
print( a )

4b751f46541adca1138efad7fbc79ccd
4b751f46541adca1138efad7fbc79ccd
0011010001100010001101110011010100110001011001100011010000110110001101010011010000110001011000010110010001100011011000010011000100110001001100110011100001100101011001100110000101100100001101110110011001100010011000110011011100111001011000110110001101100100


In [9]:

# 키값 2진수 변환 실험
f = open( 'Yek.br', 'w', encoding='utf-8' )
f.write( a )
f.close()


In [ ]:
f = open( 'Yek.br', 'r', encoding='utf-8' )
key = f.read()
f.close()

key = Encod10to2( key )

f = open( 'Yek.br', 'w', encoding='utf-8' )
f.write( key )
f.close()

In [ ]:
li_num[10]

'1'

In [ ]:
key

'001100000011000000110001001100010011000000110001001100000011000000110000001100010011000100110000001100000011000000110001001100000011000000110000001100010011000100110000001100010011000100110001001100000011000000110001001100010011000000110001001100000011000100110000001100000011000100110001001100000011000000110000001100010011000000110001001100010011000000110000001100010011000100110000001100000011000000110001001100010011000000110001001100000011000000110000001100000011000100110001001100000011000100110001001100000011000000110000001100010011000100110000001100010011000000110001001100000011000000110001001100010011000000110001001100000011000000110000001100000011000100110001001100000011000000110000001100010011000000110001001100010011000000110000001100000011000000110001001100000011000100110001001100000011000000110001001100000011000000110000001100010011000100110000001100000011000000110001001100010011000000110001001100010011000000110000001100000011000000110001001100000011000000110001001100010011000

In [ ]:
# 문자열 슬라이스 입력 시리험
a = '1234567890asadgarhgh'
b = a[8:]
b

'90asadgarhgh'

너무 난잡해서 전 실험 소스들

In [ ]:
js_data

{'boxOfficeResult': {'boxofficeType': '일별 박스오피스',
  'showRange': '20240228~20240228',
  'dailyBoxOfficeList': [{'rnum': '1',
    'rank': '1',
    'rankInten': '0',
    'rankOldAndNew': 'OLD',
    'movieCd': '20234675',
    'movieNm': '파묘',
    'openDt': '2024-02-22',
    'salesAmt': '3082228642',
    'salesShare': '59.0',
    'salesInten': '245556266',
    'salesChange': '8.7',
    'salesAcc': '31464198045',
    'audiCnt': '384605',
    'audiInten': '86139',
    'audiChange': '28.9',
    'audiAcc': '3312970',
    'scrnCnt': '1885',
    'showCnt': '7156'},
   {'rnum': '2',
    'rank': '2',
    'rankInten': '3',
    'rankOldAndNew': 'OLD',
    'movieCd': '20236295',
    'movieNm': '듄: 파트2',
    'openDt': '2024-02-28',
    'salesAmt': '1447201430',
    'salesShare': '27.7',
    'salesInten': '1327081800',
    'salesChange': '1104.8',
    'salesAcc': '1596871060',
    'audiCnt': '152956',
    'audiInten': '146129',
    'audiChange': '2140.5',
    'audiAcc': '161613',
    'scrnCnt': '1544',

In [ ]:
import requests
import numpy as np
import datetime as dt
from bs4 import BeautifulSoup

# 크롤링 할 사이트 주소
URL = 'https://www.kobis.or.kr/kobis/business/stat/boxs/findDailyBoxOfficeList.do'

# 사이트에 정보를 요청
respoonse = requests.post(URL, headers = {} )

# 받아온 정보를 BeautifulSoup 으로 파싱 할수 있는 데이터로 변환
soup = BeautifulSoup( respoonse.text, 'html.parser' )

# soup 안에서 input의 데이터를 찾는다
get_str = soup.find('input')
# temp = get_str.find('value=')
# get_str
# temp

# get_str 타입을 str 형식으로 변환
tag_str = str(get_str)

# 문자열에서 'value='의 시작 인덱스를 가져옴
# tag_str.index( 'value=' )



# len( 'value="' )
# tag_str[ 38 + 5 ]

# print( tag_str[ 38 + len('value="') ], '\n' )
# print( tag_str[ 38 + len('value="') + 1], '\n'  )
# print( tag_str )

# 문자열 길이 확인
# len( tag_str[ 38 + len('value="') : -3 ] )

# 문자열에서 필요한 문자열의 시작과 끝을 잘라서 가져옴
token = tag_str[ tag_str.index( 'value="' ) + len('value="') : -3 ]
print( token )

date_str = dt.datetime.now().strftime('%Y%m')  + str( dt.datetime.now().day -1 )

datas = {
    'CSRFToken' : token,
    'loadEnd' : 0,
    'searchType' : 'search',
    'sSearchFrom' : date_str,
    'sSearchTo' : date_str,
    'sMultiMovieYn' : '',
    'sRepNationCd' : '',
    'sWideAreaCd' : '',
}


respoonse = requests.post(URL, headers = {}, data=datas )

soup = BeautifulSoup( respoonse.text, 'html.parser' )

to_str = str( soup )

# print( to_str.find('</a>') )
#  to_str.find('</a>')

# to_str.find('tbody_0')
# print( to_str[ to_str.find('tbody_0'): ] )
# 첫번째 tbody_0 찾음
# to_str[ to_str.find('tbody_0'): ].find('<a')

# num_01 = to_str.find('tbody_0')
# num_02 = to_str[ num_01: ].find( '<a' )
# print( to_str[ num_01 + num_02: ] )
# str_temp = to_str[ num_01 + num_02: ]
# str_temp.find( '</a>' )

# print( str_temp[:77] )

# 영화 이름 가져오기 대충 성공 
# num_01 = to_str.find('tbody_0')
# num_02 = to_str[ num_01: ].find( '<a' )
# str_temp = to_str[ num_01 + num_02: ]
# str_temp.find( '</a>' )
# print( str_temp[:77] )

# print( to_str[ num_01 + num_02: ] )


# for a in soup:
#     print( a, 'asadf\n' )

# get_str = soup.find('CSRFToken')
# print( get_str )
# temp = ''
# num = 0

# for get_str in soup:
#     print( get_str, 'aaa\n' )
    # if get_str == '<head>':
    #     temp = get_str
    #     break
    # num+=1

# num, temp

# print( num, '\n', temp )
# temp

# if html_str.find('CSRFToken'):
#     print( '찾았다' )


# html_str.split('\n')
# num = 0
# temp = ''
# for r_str in html_str:
#     print( r_str, '\n' )
#     if r_str == 'name="CSRFToken"':
#         print( '찾았다' )
#         temp = r_str
#         break
#     pass

# temp

# html_str.find('CSRFToken')
# html_str.index('CSRFToken')

# type( html_str )
# html_str.find('영화')
# html_str.find('input')
# html_str.find('/"CSRFToken\"')
# html_str.find('CSRF')


# if html_str.find('CSRFToken'):
#     print('찾았다')
#     # html_str.index('CSRFToken')
#     print( html_str.index('CSRFToken') )
#     pass

# 문자열로 <a 찾기 원하는 <a 가 아님
# title = []
# temp = ''
# num01 = 0
# for i in range( 0, len( to_str ) - len( '</script>\n</body>\n</html>' )  ):
#     temp = to_str[i]
#     if to_str[i] == '<' and to_str[ i+1 ] == 'a':
#         num01 = i
#         break
#         pass
#     pass

# print( to_str[ num01 : ] )

# temp_str = to_str.split( ' ' )
# i_str = []
# for i in range( 0, len( temp_str ) - len( '</html>' ) ):
#     # print( i )
#     if temp_str[ i ].find( 'title=' ):
#         # print( '들어옴' )
#         i_str.append( temp_str[ i ] )
#         pass
#     pass
# print( i_str )
# len( i_str )

# for i in i_str:
#     print( i )
#     pass

# num01 = to_str.find( '<a' )
# i_str = []
# i_num = 0
# for i in range( 0, len( temp_str ) ):

#     if temp_str[i] == 'title=' :
#         print( '들어옴' )
#         i_str.append( temp_str[i] )
#         i_num = i
#         break
#     pass

# print( i_str )
# print( i_num )
# print( temp_str[ i_num ] )

# 해당 thml 파일에서 쉽게 클레스 구조를 알려면 개발자모드 해당 찾는 문자 검사 > 마우스 왼쪽 > copy > copy selector
# temp_str = soup.select( '#tbody_0 > tr:nth-child(1) > td.tal > span.ellip.per90 > a' )
# temp_str

# for i in temp_str:
#     print( i, '\n\n' )

# dir( temp_str )


# print( to_str )

temp_str = soup.select( '#tbody_0' )

# 데이터가 모두 한덩어리라는거 확인
# for i in temp_str:
#     print( i, '###########\n' )

# type( temp_str[0] )
# dir( temp_str[0] )

# type( temp_str )
# print( temp_str[0].text )
# title_str =  
# temp_str[0].select_one( 'title=' )
# type( title_str )
# print( temp_str[0].select( '#ellip per90 ' ) )
# print( temp_str[0].select_one('a[href]'), '끝' )

# 어거지로 파싱 성공
# tmp_str01 = str( temp_str[0].select( 'a' ) )
# tmp_str01[ tmp_str01.find( 'title' ) : tmp_str01.find( '>' ) ]

str_array = []
for i in temp_str[0].select( 'a' ):
    str_array.append( i )
    # print( i )
    pass
# str_array

str_title = []
for title in str_array:
    temp = ''
    temp = str( title )
    str_title.append( temp[ temp.find( 'title' ) + len( 'title="' ) : temp.find( '>' ) -1 ] )
    # print( temp )
    # temp.find(title)
    pass

str_title


yrn1TO4JEDusfM-fK9K9GJec_dk6m7JfECliD-a7dCs


['파묘',
 '듄: 파트2',
 '웡카',
 '건국전쟁',
 '귀멸의 칼날: 인연의 기적, 그리고 합동 강화 훈련으로',
 '소풍',
 '추락의 해부',
 '극장판 츠루네: 시작의 한 발',
 '월레스와 그로밋 더 클래식 컬렉션',
 '사운드 오브 프리덤']

In [ ]:
tag_str.index( 'value="' )

38

In [ ]:
print( respoonse.text )







<!DOCTYPE HTML>
<html lang="ko">
<head>
<meta charset="utf-8">
<title>KOFIC 영화관 입장권 통합전산망 :: 일별 박스오피스</title>
<!-- 공통 js/css -->






<!--[if IE]>
<script src="/kobis/web/comm/commjs/html5shiv.js"></script>
<![endif]-->



<!-- 기본 css -->
<link rel="stylesheet" type="text/css" href="/kobis/web/comm/commcss/default.css">
<link rel="stylesheet" type="text/css" href="/kobis/web/comm/commcss/jquery-ui-1.12.1.min.css" />
<link rel="stylesheet" type="text/css" href="/kobis/web/comm/commcss/common.css" />

<script type="text/javascript" src="/kobis/web/comm/commjs/jquery-1.12.4.min.js"></script>
<script type="text/javascript" src="/kobis/web/comm/commjs/jquery.dotdotdot.min.js"></script>
<script type="text/javascript" src="/kobis/web/comm/commjs/jquery.bxslider.js"></script>
<script type="text/javascript" src="/kobis/web/comm/commjs/comm_script.js"></script>
<script type="text/javascript" src="/kobis/web/comm/commjs/jquery-ui-1.12.1.min.js"></script>
<script type="text/javascript" src=

In [ ]:
len( 'ffUgyCMGYQ7kYfEVCs2Fe-4D6orUZJ9ydVKMbtsK72U' )

43

In [ ]:
respoonse

<Response [200]>

In [ ]:
soup.text[4]

'\n'

In [ ]:
soup


<!DOCTYPE HTML>

<html lang="ko">
<head>
<meta charset="utf-8"/>
<title>KOFIC 영화관 입장권 통합전산망 :: 일별 박스오피스</title>
<!-- 공통 js/css -->
<!--[if IE]>
<script src="/kobis/web/comm/commjs/html5shiv.js"></script>
<![endif]-->
<!-- 기본 css -->
<link href="/kobis/web/comm/commcss/default.css" rel="stylesheet" type="text/css"/>
<link href="/kobis/web/comm/commcss/jquery-ui-1.12.1.min.css" rel="stylesheet" type="text/css">
<link href="/kobis/web/comm/commcss/common.css" rel="stylesheet" type="text/css"/>
<script src="/kobis/web/comm/commjs/jquery-1.12.4.min.js" type="text/javascript"></script>
<script src="/kobis/web/comm/commjs/jquery.dotdotdot.min.js" type="text/javascript"></script>
<script src="/kobis/web/comm/commjs/jquery.bxslider.js" type="text/javascript"></script>
<script src="/kobis/web/comm/commjs/comm_script.js" type="text/javascript"></script>
<script src="/kobis/web/comm/commjs/jquery-ui-1.12.1.min.js" type="text/javascript"></script>
<script src="/kobis/web/comm/commjs/jquery.ui.date

In [ ]:
import requests
import numpy as np
import datetime as dt
import json
from bs4 import BeautifulSoup

#	http://kobis.or.kr/kobisopenapi/webservice/rest/boxoffice/searchDailyBoxOfficeList.json?key=f5eef3421c602c6cb7ea224104795888&targetDt=20120101

date_str = dt.datetime.now().strftime('%Y%m')  + str( dt.datetime.now().day -1 )
# date_str = dt.datetime.now().strftime('%Y%m%d')

# 접속할 사이트
URL = f'http://kobis.or.kr/kobisopenapi/webservice/rest/boxoffice/searchDailyBoxOfficeList.json?key={key}&targetDt={date_str}'

# URL = f'http://kobis.or.kr/kobisopenapi/webservice/rest/boxoffice/searchDailyBoxOfficeList.json?key=4b751f46541adca1138efad7fbc79ccd&targetDt=20240221'


# data = {
#     'loadEnd' : 0,
#     'searchType' : 'search',
#     'sSearchFrom' :'2024-02-14',
#     'sSearchTo' : '2024-02-21',
#     'sMultiMovieYn' : '',
#     'sRepNationCd' : '',
#     'sWideAreaCd' : '',
# }

datas = {
'boxOfficeResult':{
    'boxofficeType' : '일별박스오피스',
    'showRange' : '20240221~20240221',
    'dailyBoxOfficeList' : [], 
    } }
    

# datas = {
#     'boxofficeType' : '일별박스오피스',
#     'showRange' : '20240221~20240221',
#     'dailyBoxOfficeList' : [] 
#     }

# datas = {
# 'boxOfficeResult':{
#     'boxofficeType' : '일별박스오피스',
#     'showRange' : '20240221~20240221',
#     'dailyBoxOfficeList' : [
#         {
#             'rnum':'',
#             'rank':'',
#             'rankInten':'',
#             'rankOldAndNew':'',
#             'movieCd':'',
#             'movieNm':'',
#             'openDt':'',
#             'salesAmt':'',
#             'salesShare':'',
#             'salesInten':'',
#             'salesChange':'',
#             'salesAcc':'',
#             'audiCnt':'',
#             'audiInten':'',
#             'audiChange':'',
#             'audiAcc':'',
#             'scrnCnt':'',
#             'showCnt':'',
#             },
#     ], 
#     } }
    

headers={
    # 'CSRFToken' : '1fuqgLYICAkt-GoG3ApkdvhZQUsCo5yXBmjhzed5sZ4',
    }

# header={
#     'User-Agent' : 'Mozilla/5.0',
#     }
# ur = 'https://www.kobis.or.kr/kobis/web/comm/commcss/default.css'
# respoonse = requests.post(ur, headers = headers )
respoonse = requests.get(URL, headers = headers, data = datas )
# respoonse = requests.post(URL, headers = header, data = datas )
# respoonse = requests.post(URL, headers = headers )

js_data = json.loads( respoonse.text )


# soup = BeautifulSoup( respoonse.text, 'html.parser' )

In [ ]:
js_data

{'faultInfo': {'message': '알수없는 오류가 발생했습니다.', 'errorCode': '320099'}}

In [ ]:
respoonse.json()

{'faultInfo': {'message': '알수없는 오류가 발생했습니다.', 'errorCode': '320099'}}

In [ ]:
http://kobis.or.kr/kobisopenapi/webservice/rest/boxoffice/searchDailyBoxOfficeList.json?key=4b751f46541adca1138efad7fbc79ccd&targetDt=20240221

SyntaxError: invalid decimal literal (3629827719.py, line 1)

In [ ]:
datas

{'boxOfficeResult': {'boxofficeType': '일별박스오피스',
  'showRange': '20240221~20240221',
  'dailyBoxOfficeList': []}}

In [ ]:
print( respoonse.text )

In [ ]:
respoonse

<Response [200]>

In [ ]:
data

{}

In [ ]:
'''CSRFToken: 1fuqgLYICAkt-GoG3ApkdvhZQUsCo5yXBmjhzed5sZ4
loadEnd: 0
searchType: search
sSearchFrom: 2024-02-14
sSearchTo: 2024-02-21
sMultiMovieYn: 
sRepNationCd: 
sWideAreaCd: '''

In [ ]:
'https://www.kobis.or.kr/kobis/business/stat/boxs/findDailyBoxOfficeList.do'

'https://www.kobis.or.kr/kobis/business/stat/boxs/findDailyBoxOfficeList.do'

In [ ]:
soup

In [ ]:
respoonse

<Response [200]>

In [ ]:
print( respoonse.text )

In [ ]:
def shuffle_num( x_num, y_num ):
    temp = x_num
    x_num = y_num
    y_num = temp
    return x_num, y_num

f = open( '영진위 api.txt', 'r', encoding='utf-8' )
in_str = f.read()
f.close()



f = open( 'Yek.br', 'w', encoding='utf-8' )
f.write( in_str )
f.close()
in_str

'4b751f46541adca1138efad7fbc79ccd'

In [ ]:
import numpy as np
np.random.randint(0, 5, 5)

array([0, 1, 3, 1, 1])

In [ ]:
import time

def shuffle_num( x_num, y_num ):
    temp = x_num
    x_num = y_num
    y_num = temp
    return x_num, y_num

def shuffle_array( num, for_num ):
    if len(num) < 0:
        return 
    for i in range( 0, for_num ):
        i = int( time.time() % len(num) )
        time.sleep(0.5)
        # print(i)
        j = int( time.time() % len(num) )
        # print(j)
        temp = num[i]
        num[i] = num[j]
        num[j] = temp
    return num

num = [ 1, 2, 3, 4, 5, 6, 7, 8, 9 ]
# shuffle = np.random.randint(1, 9, 8)
print( num )
# print( shuffle )

int( time.time() % len(num) )
num01 = []
# for i in range(0 , 50):
#     num01 = shuffle_array( num )
num01 = shuffle_array( num, 10 )

temp = {}

for i in range( 0, len( num01 ) ):
    temp[ str( i ) ] = bin( num01[i] )


num
num01
temp
num02 = []

for i in temp:
    # print( i )
    # num01 = temp[ i ]
    num02.append( int( temp[ i ], 2 ) )
    pass
print( num01 ) 
print( temp )
# print( num01)

# int( temp['0'], 2 )

# new_dic = {}

for i in temp:
    print( int( temp[i], 2) ) 
    pass



    


[1, 2, 3, 4, 5, 6, 7, 8, 9]
[2, 6, 3, 4, 5, 7, 8, 9, 1]
{'0': '0b10', '1': '0b110', '2': '0b11', '3': '0b100', '4': '0b101', '5': '0b111', '6': '0b1000', '7': '0b1001', '8': '0b1'}
2
6
3
4
5
7
8
9
1


In [ ]:
def shuffle_num( x_num, y_num ):
    temp = x_num
    x_num = y_num
    y_num = temp
    return x_num, y_num

def shuffle_array( num ):
    if len(num) < 0:
        return 
    temp = num[0]
    num[0] = num[1]
    num[1] = temp
    return num


# shuffle( 1, 2 )
shuffle( [1, 2] )


NameError: name 'shuffle' is not defined

In [ ]:
import datetime as dt
x = dt.datetime.now()
type(x.year)
in_str = x.strftime( '%Y%m' ) + str( x.day -1 )
in_str

'20240222'

In [ ]:
import time
time.time()

1708670476.4210734

In [ ]:
a = 'assdfawegtearhgaerg'

a.find('g')
a.index('g')

8

In [ ]:
import numpy as np
# np.random.randint( 0, 9, replace = False )

np.random.randint( 1, 9, 9, replace = False)

TypeError: randint() got an unexpected keyword argument 'replace'

In [ ]:
print( '</a>' )

</a>


In [ ]:
num = 112314
f = open( 'BoxOffice.sav', 'w', encoding='utf-8' )
f.write( num )
f.close()

TypeError: write() argument must be str, not int

In [ ]:
f = open( 'BoxOffice.sav', 'r', encoding='utf-8' )
open_file = json.load( f )
f.close()

# print( open_file )
# open_file

# for i in open_file:
#     print( i )
#     pass 

for i in open_file['20240226']:
    print( i['movieNm'] )
    pass



파묘
웡카
건국전쟁
귀멸의 칼날: 인연의 기적, 그리고 합동 강화 훈련으로
소풍
사운드 오브 프리덤
시민덕희
바튼 아카데미
아기상어 극장판: 사이렌 스톤의 비밀
기적의 시작


In [ ]:
open_file['20240226'][0]['movieNm']

'파묘'

In [ ]:
f = open( 'Yek.br', 'r', encoding='utf-8' )
num = f.read()
f.close()

num

''

In [ ]:
f = open( 'test.br', 'w', encoding='utf-8' )
f.write( '4b751f46541adca1138efad7fbc79ccd' )
f.close()



In [ ]:
import numpy as np

def shuffle_array( num, for_num ):
    if len(num) < 0:
        return 
    Key = []    
    for i in range( 0, for_num ):
        # i = int( time.time() % len(num) )
        # time.sleep(0.5)
        # print(i)
        # j = int( time.time() % len(num) )
        # print(j)

        i, j = np.random.choice(range(0, len( num )), 2, replace=False)
        temp = num[i]
        num[i] = num[j]
        num[j] = temp
    return num

f = open( 'test.br', 'r', encoding='utf-8' )
num = f.read()
f.close()

# num.split('')
new_num = shuffle_array( list(num), 20 )
new_num = ''.join( new_num )
# ' '.split( num )
num
new_num

print( num  )
print( new_num  )


4b751f46541adca1138efad7fbc79ccd
4e754f165417cac17da18bfc9ddacb3f


In [ ]:
import numpy as np

# 1~45 중 중복 없이 6개 숫자 추출
numbers = np.random.choice(range(1, 46), 6, replace=False)
numbers

array([13, 34, 30, 21, 16, 15])

In [ ]:

i, j = np.random.choice(range(0, 9), 2, replace=False)
i , j

(7, 8)

In [ ]:
import sys

sys.getsizeof( 1 )

28

In [ ]:
f = open( 'test.br', 'r', encoding='utf-8' )
num = f.read()
f.close()

int_num = []


TypeError: ord() expected a character, but string of length 32 found

In [ ]:
f = open( 'BoxOffice.txt', 'r', encoding='utf-8' )
data = json.load( f )
f.close()

# f = open( 'BoxOffice.sav', 'r', encoding='utf-8' )
# data01 = json.load( f )
# f.close()

# print( data )
data

{'20240227': [{'rnum': '1',
   'rank': '1',
   'rankInten': '0',
   'rankOldAndNew': 'OLD',
   'movieCd': '20234675',
   'movieNm': '파묘',
   'openDt': '2024-02-22',
   'salesAmt': '2836712376',
   'salesShare': '73.4',
   'salesInten': '-291557207',
   'salesChange': '-9.3',
   'salesAcc': '28382091403',
   'audiCnt': '298472',
   'audiInten': '-29975',
   'audiChange': '-9.1',
   'audiAcc': '2928378',
   'scrnCnt': '2145',
   'showCnt': '8359'},
  {'rnum': '2',
   'rank': '2',
   'rankInten': '0',
   'rankOldAndNew': 'OLD',
   'movieCd': '20236180',
   'movieNm': '웡카',
   'openDt': '2024-01-31',
   'salesAmt': '383104408',
   'salesShare': '9.9',
   'salesInten': '21526649',
   'salesChange': '6',
   'salesAcc': '29442870773',
   'audiCnt': '42088',
   'audiInten': '3299',
   'audiChange': '8.5',
   'audiAcc': '3051510',
   'scrnCnt': '777',
   'showCnt': '2352'},
  {'rnum': '3',
   'rank': '3',
   'rankInten': '0',
   'rankOldAndNew': 'OLD',
   'movieCd': '20247074',
   'movieNm': '건

In [ ]:
# API를 이용해서 데이터 받아오기
import requests
import datetime as dt
import json

f = open( 'Yek.br', 'r', encoding='utf-8' )
key = f.read()
f.close()

# 키값
# key = '4b751f46541adca1138efad7fbc79ccd'
# 하루전 날자를 받는다
date_str = dt.datetime.now().strftime('%Y%m')  + str( dt.datetime.now().day -7 )

# 접속할 사이트
URL = f'http://kobis.or.kr/kobisopenapi/webservice/rest/boxoffice/searchDailyBoxOfficeList.json?key={key}&targetDt={date_str}'

# 사이트에 요청
respoonse = requests.get(URL, headers = {} )

# 사이트에서 받아온 값을 json 형식을 파일을 변환
js_data = json.loads( respoonse.text )

# json 형식의 파일 안에서 boxOfficeResult에 dailyBoxOfficeList의 데이터를 가져옴
# daily_data의 딕셔너리에 키 값으로 날자( YYYYMMDD 형식 ) 넣고 
# 데이터 값에 boxOfficeResult에 dailyBoxOfficeList의 데이터를 리스트 형식으로 넣는다
daily_data = { date_str : js_data[ 'boxOfficeResult']['dailyBoxOfficeList' ] }


# daily_data[ '02342485' ] = 13

# 데이터 출력
# for day in daily_data:
#     # if day.get('day', 0):
#         # continue
#     for data in daily_data[ day ]:
#         n_or_o = ''
#         if data['rankOldAndNew'] == 'OLD':
#             n_or_o = '기존'
#         else:
#             n_or_o = '신규'
            
#         print( data['rank'] + ' ' + data['movieNm'] + ' ' + n_or_o  )
#         pass
#     pass

# str_data =  str( daily_data )

# print( str_data )
# str_data

# str_data

# 파일 저장 계속 추가 됨으로 저장할때만 풀것
f = open( 'BoxOffice.txt', 'a', encoding='utf-8' )
json.dump( str_data, f )
f.close()

f = open( 'BoxOffice.txt', 'r' )
tmep_json = json.load( f )
# temp_str = f.read()
# tmep_json = json.load( f )
f.close()



for key in  daily_data.keys():
    tmep_json[ key ] = daily_data[ key ]
print( temp_str )

daily_data[ '20240221' ]
tmep_json


# f = open( 'BoxOffice.txt', 'w' )
# json.dump( tmep_json, f )
# f.close()

In [ ]:
temp_str

"{'20240227': [{'rnum': '1', 'rank': '1', 'rankInten': '0', 'rankOldAndNew': 'OLD', 'movieCd': '20234675', 'movieNm': '파묘', 'openDt': '2024-02-22', 'salesAmt': '2836712376', 'salesShare': '73.4', 'salesInten': '-291557207', 'salesChange': '-9.3', 'salesAcc': '28382091403', 'audiCnt': '298472', 'audiInten': '-29975', 'audiChange': '-9.1', 'audiAcc': '2928378', 'scrnCnt': '2145', 'showCnt': '8359'}, {'rnum': '2', 'rank': '2', 'rankInten': '0', 'rankOldAndNew': 'OLD', 'movieCd': '20236180', 'movieNm': '웡카', 'openDt': '2024-01-31', 'salesAmt': '383104408', 'salesShare': '9.9', 'salesInten': '21526649', 'salesChange': '6', 'salesAcc': '29442870773', 'audiCnt': '42088', 'audiInten': '3299', 'audiChange': '8.5', 'audiAcc': '3051510', 'scrnCnt': '777', 'showCnt': '2352'}, {'rnum': '3', 'rank': '3', 'rankInten': '0', 'rankOldAndNew': 'OLD', 'movieCd': '20247074', 'movieNm': '건국전쟁', 'openDt': '2024-02-01', 'salesAmt': '170530355', 'salesShare': '4.4', 'salesInten': '7214792', 'salesChange': '4.4

In [ ]:
# datas = temp_str.split('}')

str_datas = temp_str.split(']')

dict_str = {}
list_temp = []

for i in str_datas:
    # print( i )
    list_temp.append( i )
    break

# datas
# type( list_temp[0] )
title, str_data = list_temp[0].split('[')
print( title + '\n' )
# print( str_data )
# str_data
# str_datas[1]

# if ord( title[0] )
title.strip( '{' )


{'20240227': 



"'20240227': "

"{'20240227': [{'rnum': '1', 'rank': '1', 'rankInten': '0', 'rankOldAndNew': 'OLD', 'movieCd': '20234675', 'movieNm': '파묘', 'openDt': '2024-02-22', 'salesAmt': '2836712376', 'salesShare': '73.4', 'salesInten': '-291557207', 'salesChange': '-9.3', 'salesAcc': '28382091403', 'audiCnt': '298472', 'audiInten': '-29975', 'audiChange': '-9.1', 'audiAcc': '2928378', 'scrnCnt': '2145', 'showCnt': '8359'}, {'rnum': '2', 'rank': '2', 'rankInten': '0', 'rankOldAndNew': 'OLD', 'movieCd': '20236180', 'movieNm': '웡카', 'openDt': '2024-01-31', 'salesAmt': '383104408', 'salesShare': '9.9', 'salesInten': '21526649', 'salesChange': '6', 'salesAcc': '29442870773', 'audiCnt': '42088', 'audiInten': '3299', 'audiChange': '8.5', 'audiAcc': '3051510', 'scrnCnt': '777', 'showCnt': '2352'}, {'rnum': '3', 'rank': '3', 'rankInten': '0', 'rankOldAndNew': 'OLD', 'movieCd': '20247074', 'movieNm': '건국전쟁', 'openDt': '2024-02-01', 'salesAmt': '170530355', 'salesShare': '4.4', 'salesInten': '7214792', 'salesChange': '4.4

In [ ]:
tmep_json['20240227'][0]

{'rnum': '1',
 'rank': '1',
 'rankInten': '0',
 'rankOldAndNew': 'OLD',
 'movieCd': '20234675',
 'movieNm': '파묘',
 'openDt': '2024-02-22',
 'salesAmt': '2836712376',
 'salesShare': '73.4',
 'salesInten': '-291557207',
 'salesChange': '-9.3',
 'salesAcc': '28382091403',
 'audiCnt': '298472',
 'audiInten': '-29975',
 'audiChange': '-9.1',
 'audiAcc': '2928378',
 'scrnCnt': '2145',
 'showCnt': '8359'}

In [ ]:
tmep_json

f = open( 'BoxOffice.txt', 'w' )
f.write( str( tmep_json ) )
f.close()

In [ ]:
f = open( 'BoxOffice.txt', 'r' )
red_str = f.read()
f.close()

red_str.replace('\'','')

# r_01 = json.load( red_str )

'{20240227: [{rnum: 1, rank: 1, rankInten: 0, rankOldAndNew: OLD, movieCd: 20234675, movieNm: 파묘, openDt: 2024-02-22, salesAmt: 2836712376, salesShare: 73.4, salesInten: -291557207, salesChange: -9.3, salesAcc: 28382091403, audiCnt: 298472, audiInten: -29975, audiChange: -9.1, audiAcc: 2928378, scrnCnt: 2145, showCnt: 8359}, {rnum: 2, rank: 2, rankInten: 0, rankOldAndNew: OLD, movieCd: 20236180, movieNm: 웡카, openDt: 2024-01-31, salesAmt: 383104408, salesShare: 9.9, salesInten: 21526649, salesChange: 6, salesAcc: 29442870773, audiCnt: 42088, audiInten: 3299, audiChange: 8.5, audiAcc: 3051510, scrnCnt: 777, showCnt: 2352}, {rnum: 3, rank: 3, rankInten: 0, rankOldAndNew: OLD, movieCd: 20247074, movieNm: 건국전쟁, openDt: 2024-02-01, salesAmt: 170530355, salesShare: 4.4, salesInten: 7214792, salesChange: 4.4, salesAcc: 9401329857, audiCnt: 19498, audiInten: 858, audiChange: 4.6, audiAcc: 1004672, scrnCnt: 645, showCnt: 1464}, {rnum: 4, rank: 4, rankInten: 0, rankOldAndNew: OLD, movieCd: 202470

In [ ]:
red_str.replace('\'','')

'{20240227: [{rnum: 1, rank: 1, rankInten: 0, rankOldAndNew: OLD, movieCd: 20234675, movieNm: 파묘, openDt: 2024-02-22, salesAmt: 2836712376, salesShare: 73.4, salesInten: -291557207, salesChange: -9.3, salesAcc: 28382091403, audiCnt: 298472, audiInten: -29975, audiChange: -9.1, audiAcc: 2928378, scrnCnt: 2145, showCnt: 8359}, {rnum: 2, rank: 2, rankInten: 0, rankOldAndNew: OLD, movieCd: 20236180, movieNm: 웡카, openDt: 2024-01-31, salesAmt: 383104408, salesShare: 9.9, salesInten: 21526649, salesChange: 6, salesAcc: 29442870773, audiCnt: 42088, audiInten: 3299, audiChange: 8.5, audiAcc: 3051510, scrnCnt: 777, showCnt: 2352}, {rnum: 3, rank: 3, rankInten: 0, rankOldAndNew: OLD, movieCd: 20247074, movieNm: 건국전쟁, openDt: 2024-02-01, salesAmt: 170530355, salesShare: 4.4, salesInten: 7214792, salesChange: 4.4, salesAcc: 9401329857, audiCnt: 19498, audiInten: 858, audiChange: 4.6, audiAcc: 1004672, scrnCnt: 645, showCnt: 1464}, {rnum: 4, rank: 4, rankInten: 0, rankOldAndNew: OLD, movieCd: 202470

"{'20240227': [{'rnum': '1', 'rank': '1', 'rankInten': '0', 'rankOldAndNew': 'OLD', 'movieCd': '20234675', 'movieNm': '파묘', 'openDt': '2024-02-22', 'salesAmt': '2836712376', 'salesShare': '73.4', 'salesInten': '-291557207', 'salesChange': '-9.3', 'salesAcc': '28382091403', 'audiCnt': '298472', 'audiInten': '-29975', 'audiChange': '-9.1', 'audiAcc': '2928378', 'scrnCnt': '2145', 'showCnt': '8359'}, {'rnum': '2', 'rank': '2', 'rankInten': '0', 'rankOldAndNew': 'OLD', 'movieCd': '20236180', 'movieNm': '웡카', 'openDt': '2024-01-31', 'salesAmt': '383104408', 'salesShare': '9.9', 'salesInten': '21526649', 'salesChange': '6', 'salesAcc': '29442870773', 'audiCnt': '42088', 'audiInten': '3299', 'audiChange': '8.5', 'audiAcc': '3051510', 'scrnCnt': '777', 'showCnt': '2352'}, {'rnum': '3', 'rank': '3', 'rankInten': '0', 'rankOldAndNew': 'OLD', 'movieCd': '20247074', 'movieNm': '건국전쟁', 'openDt': '2024-02-01', 'salesAmt': '170530355', 'salesShare': '4.4', 'salesInten': '7214792', 'salesChange': '4.4

In [ ]:
tmep_json

{'20240227': [{'rnum': '1',
   'rank': '1',
   'rankInten': '0',
   'rankOldAndNew': 'OLD',
   'movieCd': '20234675',
   'movieNm': '파묘',
   'openDt': '2024-02-22',
   'salesAmt': '2836712376',
   'salesShare': '73.4',
   'salesInten': '-291557207',
   'salesChange': '-9.3',
   'salesAcc': '28382091403',
   'audiCnt': '298472',
   'audiInten': '-29975',
   'audiChange': '-9.1',
   'audiAcc': '2928378',
   'scrnCnt': '2145',
   'showCnt': '8359'},
  {'rnum': '2',
   'rank': '2',
   'rankInten': '0',
   'rankOldAndNew': 'OLD',
   'movieCd': '20236180',
   'movieNm': '웡카',
   'openDt': '2024-01-31',
   'salesAmt': '383104408',
   'salesShare': '9.9',
   'salesInten': '21526649',
   'salesChange': '6',
   'salesAcc': '29442870773',
   'audiCnt': '42088',
   'audiInten': '3299',
   'audiChange': '8.5',
   'audiAcc': '3051510',
   'scrnCnt': '777',
   'showCnt': '2352'},
  {'rnum': '3',
   'rank': '3',
   'rankInten': '0',
   'rankOldAndNew': 'OLD',
   'movieCd': '20247074',
   'movieNm': '건